# Exercise Session 10 - Old Exam Questions

## SQL

In [1]:
%load_ext sql
%sql postgresql://postgres:example@db

Connecting to 'postgresql://postgres:***@db'

<img src="https://polybox.ethz.ch/index.php/s/8CqNffQrR0EDbuC/download" width=800/>

What is the number of artists that have released less than three releases with the genre 'Pop' and more than five releases with the genre 'Rock'?
> Remember: no Pop releases also means < 3 Pop releases.

In [2]:
%%sql


UsageError: %%sql is a cell magic, but the cell body is empty. Did you mean the line magic %sql (single %)?


What is the name of the artist who has the highest number of releases in country "Switzerland"?

In [ ]:
%%sql


## Spark

##### For more information on Spark (e.g. for creation functions), use ``help``:

In [3]:
import json

from pyspark import SparkContext, RDD
from jsoniq import RumbleSession

spark = RumbleSession \
    .builder \
    .master("local[*]") \
    .getOrCreate()

sc = spark.sparkContext

25/12/03 16:21:38 WARN NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable
Using Spark's default log4j profile: org/apache/spark/log4j2-defaults.properties
Setting default log level to "WARN".
To adjust logging level use sc.setLogLevel(newLevel). For SparkR, use setLogLevel(newLevel).


### SparkSQL and Spark Dataframes

In [4]:
%load_ext sparksql_magic

orders_path = "orders.jsonl"
orders_df = spark.read.json(orders_path)
orders_df.createOrReplaceTempView("orders")

confusion_path = "confusion-2014-03-02/confusion-part.json"
dataset = spark.read.json(confusion_path).cache()
dataset.createOrReplaceTempView("dataset")

Inspect the dataset by printing the first row:

In [5]:
from pyspark.sql.functions import explode

orders_df.limit(1).show(vertical=True, truncate=False)
orders_df.printSchema()
orders_df.select(explode("items").alias('item'), 'item.quantity', 'item.price').describe().show()

-RECORD 0---------------------------------------------------------------------------------------------------------------------------------------------------------------------
 customer | {Preston, Landry}                                                                                                                                                 
 date     | 2018-2-4                                                                                                                                                          
 items    | [{1.53, fan, 5}, {1.33, computer screen, 6}, {1.06, kettle, 6}, {1.96, stuffed animal, 3}, {1.09, the book, 7}, {1.42, headphones, 9}, {1.67, whiskey bottle, 3}] 
 order_id | 0                                                                                                                                                                 

root
 |-- customer: struct (nullable = true)
 |    |-- first_name: string (nullable = true)
 |    |-- last_name: string (nul

Now it's your turn: you can write all your queries in new cells below. Feel free to add as many cells as needed.

In [6]:
# Snooze Copilot. ;)
# How many unique customers ordered the product "stuffed animal"


In [7]:
%%sparksql


UsageError: %%sparksql is a cell magic, but the cell body is empty.


In [ ]:
# How many unique customers ordered the product "stuffed animal"
orders_df.rdd


In [ ]:
# What is the date at which the order with the largest quantity was placed?
orders_df


In [ ]:
%%sparksql


In [ ]:
orders_df.rdd


## Quiz 9.1 and 9.2

### Assignment 4

Focus on the first playing day of August 2013. Which language had the worst accuracy?
(In case of a tie, return the language with more games played.)


In [8]:
dataset.printSchema()

root
 |-- choices: array (nullable = true)
 |    |-- element: string (containsNull = true)
 |-- country: string (nullable = true)
 |-- date: string (nullable = true)
 |-- guess: string (nullable = true)
 |-- sample: string (nullable = true)
 |-- target: string (nullable = true)



In [9]:
from pyspark.sql.functions import col, avg, asc, count, desc


In [10]:
%%sparksql


UsageError: %%sparksql is a cell magic, but the cell body is empty.


### Assignment 5

Return number of games where the guessed language is correct and it appeared last in the choices list.

Hint: Check the docs of function [`element_at`](https://spark.apache.org/docs/4.0.0/api/python/reference/pyspark.sql/api/pyspark.sql.functions.element_at.html).

In [11]:
dataset.printSchema()

root
 |-- choices: array (nullable = true)
 |    |-- element: string (containsNull = true)
 |-- country: string (nullable = true)
 |-- date: string (nullable = true)
 |-- guess: string (nullable = true)
 |-- sample: string (nullable = true)
 |-- target: string (nullable = true)



In [12]:
from pyspark.sql.functions import element_at
dataset


DataFrame[choices: array<string>, country: string, date: string, guess: string, sample: string, target: string]

In [13]:
%%sparksql


UsageError: %%sparksql is a cell magic, but the cell body is empty.


### Solutions

In [14]:
%%sql
-- question 1
WITH artists_tracks AS (
    SELECT artist_id, genre, COUNT(DISTINCT release_id) AS num_releases
    FROM artists a
    JOIN released_by USING(artist_id)
    JOIN releases r USING(release_id)
    GROUP BY artist_id, genre
),
artists_too_much_pop AS (
    SELECT artist_id, num_releases AS pop
    FROM artists_tracks
    WHERE genre = 'Pop' AND num_releases >= 3
),
artists_rock AS (
    SELECT artist_id, num_releases AS rock
    FROM artists_tracks
    WHERE genre = 'Rock' AND num_releases > 5
),
artists AS(
    SELECT artist_id
    FROM artists_rock
    EXCEPT
    SELECT artist_id
    FROM artists_too_much_pop
)
SELECT COUNT(DISTINCT artist_id)
FROM artists;

Running query in 'postgresql://postgres:***@db'

1 rows affected.

+-------+
| count |
+-------+
|  554  |
+-------+

In [15]:
%%sql
-- question 2
SELECT a.name, a.artist_id, COUNT(r.release_id) FROM
artists a
JOIN released_by rb USING(artist_id)
JOIN releases r USING(release_id)
WHERE r.country = 'Switzerland' AND a.name <> 'Various Artists'
GROUP BY a.name, a.artist_id
ORDER BY COUNT(r.release_id) DESC
LIMIT 3;


Running query in 'postgresql://postgres:***@db'

3 rows affected.

+------------+-----------+-------+
|    name    | artist_id | count |
+------------+-----------+-------+
|  DJ Noise  |   27747   |   36  |
| DJ Snowman |   12518   |   31  |
|  Dave 202  |   48644   |   27  |
+------------+-----------+-------+

In [16]:
# How many unique customers ordered the product "stuffed animal"
from pyspark.sql.functions import col, explode, array_contains

v1=(orders_df
    .filter(array_contains("items.product", "stuffed animal"))
    .select('customer.first_name', 'customer.last_name')
    .distinct()
    .count()
)
print(v1)

# Re-project!
v2 = (orders_df
    .select(explode("items").alias('item'), 'item.product', 'customer.first_name', 'customer.last_name')
    .filter(col("item.product") == "stuffed animal")
    .select('first_name', 'last_name') # very important, because otherwise we select also on the distinct item.*
    .distinct().count()
)
print(v2)

27384
27384


In [17]:
%%sparksql
SELECT COUNT(DISTINCT (customer.first_name, customer.last_name))
FROM orders LATERAL VIEW explode(items) items AS item
WHERE item.product = 'stuffed animal';

In [18]:
%%sparksql
SELECT COUNT(DISTINCT (customer.first_name, customer.last_name))
FROM orders
WHERE array_contains(items.product, 'stuffed animal');

In [19]:
orders_df.printSchema()

root
 |-- customer: struct (nullable = true)
 |    |-- first_name: string (nullable = true)
 |    |-- last_name: string (nullable = true)
 |-- date: string (nullable = true)
 |-- items: array (nullable = true)
 |    |-- element: struct (containsNull = true)
 |    |    |-- price: double (nullable = true)
 |    |    |-- product: string (nullable = true)
 |    |    |-- quantity: long (nullable = true)
 |-- order_id: long (nullable = true)



In [20]:
(orders_df.rdd
    .flatMap(lambda x: ((item['product'], x['customer']['first_name'], x['customer']['last_name']) for item in x['items']))
    .filter(lambda x: x[0] == 'stuffed animal')
    .map(lambda x: (x[1], x[2]))
    .distinct().count())

27384

In [21]:
(orders_df.rdd
    .filter(lambda x: any(item['product'] == 'stuffed animal' for item in x['items']))
    .map(lambda x: (x['customer']['first_name'], x['customer']['last_name'])).distinct().count())

27384

In [22]:
# What is the date at which the order with the largest quantity was placed?
from pyspark.sql.functions import col, explode, sum
(orders_df.select(explode("items").alias('item'), '*')
    .select('order_id', 'item.quantity', 'date')
    .groupBy('date', 'order_id')
    .agg(sum('quantity').alias('quantity'))
    .orderBy('quantity', ascending=False)
    .limit(1)
    .show()
    )

+--------+--------+--------+
|    date|order_id|quantity|
+--------+--------+--------+
|2016-3-6|   99636|      65|
+--------+--------+--------+



In [23]:
%%sparksql
SELECT order_id, date, SUM(item.quantity) AS quantity
FROM orders
LATERAL VIEW explode(items) items AS item
GROUP BY order_id, date
ORDER BY quantity DESC
LIMIT 1;

In [24]:
(orders_df.rdd
    .flatMap(lambda x: (
        ((x['order_id'], x['date']), item['quantity']) for item in x['items']
    ))
    .reduceByKey(lambda a, b: a + b)
    .map(lambda x: (x[1], x[0]))
    .sortByKey(ascending=False)
    .take(3)
)

[(65, (99636, '2016-3-6')),
 (64, (78588, '2018-4-2')),
 (63, (82807, '2016-4-10'))]

Quiz solutions:

In [25]:
# Assignment 4
from pyspark.sql.functions import avg, col, count

(
    dataset.filter(dataset["date"].between("2013-08-01", "2013-08-31"))
    .groupBy("date", "target")
    .agg(
        avg((dataset["target"] == dataset["guess"]).cast("int")).alias("accuracy"),
        count(dataset["sample"]).alias("count"),
    )
    .orderBy(dataset["date"].asc(), col("accuracy").asc(), col("count").desc(), col("target").asc())
    .limit(4)
    .show()
)

+----------+--------+--------+-----+
|      date|  target|accuracy|count|
+----------+--------+--------+-----+
|2013-08-19|Albanian|     0.0|    4|
|2013-08-19|Armenian|     0.0|    3|
|2013-08-19|   Maori|     0.0|    2|
|2013-08-19|  Samoan|     0.0|    2|
+----------+--------+--------+-----+



In [26]:
# Assignment 5
from pyspark.sql.functions import element_at
dataset.filter((dataset["target"] == dataset["guess"]) & (element_at(dataset["choices"], -1) == dataset["target"])).count()


803024